# Table of Contents
 <p><div class="lev1 toc-item"><a href="#Ground-predictions" data-toc-modified-id="Ground-predictions-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Ground predictions</a></div><div class="lev2 toc-item"><a href="#PVLib-Clearsky" data-toc-modified-id="PVLib-Clearsky-11"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>PVLib Clearsky</a></div><div class="lev1 toc-item"><a href="#Train/test-on-NSRDB-data-to-find-optimal-parameters" data-toc-modified-id="Train/test-on-NSRDB-data-to-find-optimal-parameters-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Train/test on NSRDB data to find optimal parameters</a></div><div class="lev2 toc-item"><a href="#5-min-freq-ground-data" data-toc-modified-id="5-min-freq-ground-data-21"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>5 min freq ground data</a></div><div class="lev1 toc-item"><a href="#Train-on-all-NSRDB-data,-test-various-freq-of-ground-data" data-toc-modified-id="Train-on-all-NSRDB-data,-test-various-freq-of-ground-data-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Train on all NSRDB data, test various freq of ground data</a></div><div class="lev2 toc-item"><a href="#30-min-freq-ground-data" data-toc-modified-id="30-min-freq-ground-data-31"><span class="toc-item-num">3.1&nbsp;&nbsp;</span>30 min freq ground data</a></div><div class="lev2 toc-item"><a href="#15-min-freq-ground-data" data-toc-modified-id="15-min-freq-ground-data-32"><span class="toc-item-num">3.2&nbsp;&nbsp;</span>15 min freq ground data</a></div><div class="lev2 toc-item"><a href="#10-min-freq-ground-data" data-toc-modified-id="10-min-freq-ground-data-33"><span class="toc-item-num">3.3&nbsp;&nbsp;</span>10 min freq ground data</a></div><div class="lev2 toc-item"><a href="#5-min-freq-ground-data" data-toc-modified-id="5-min-freq-ground-data-34"><span class="toc-item-num">3.4&nbsp;&nbsp;</span>5 min freq ground data</a></div><div class="lev2 toc-item"><a href="#1-min-freq-ground-data" data-toc-modified-id="1-min-freq-ground-data-35"><span class="toc-item-num">3.5&nbsp;&nbsp;</span>1 min freq ground data</a></div>

In [1]:
import pandas as pd
import numpy as np
import os
import datetime
import matplotlib
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable
from sklearn import tree

import pytz
import itertools
import visualize
import utils
import pydotplus
import xgboost as xgb

from sklearn import metrics

import pvlib
import cs_detection_refactor as cs_detection
# import cs_detection_refactor
# import visualize
# from bokeh.plotting import output_notebook
# output_notebook()

import visualize_plotly as visualize

from IPython.display import Image

%load_ext autoreload
%autoreload 2

np.set_printoptions(precision=4)
%matplotlib notebook

# Ground predictions

## PVLib Clearsky

Only making ground predictions using PVLib clearsky model and statistical model.  NSRDB model won't be available to ground measurements.

In [2]:
nsrdb = cs_detection.ClearskyDetection.read_pickle('abq_nsrdb_1.pkl.gz')
nsrdb.df.index = nsrdb.df.index.tz_convert('MST')

In [3]:
nsrdb.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [4]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')

In [5]:
feature_cols = [
'tfn',
'abs_ideal_ratio_diff',
'abs_ideal_ratio_diff mean',
'abs_ideal_ratio_diff std',
'abs_ideal_ratio_diff max',
'abs_ideal_ratio_diff min',
'GHI Clearsky GHI pvlib gradient ratio', 
'GHI Clearsky GHI pvlib gradient ratio mean', 
'GHI Clearsky GHI pvlib gradient ratio std', 
'GHI Clearsky GHI pvlib gradient ratio min', 
'GHI Clearsky GHI pvlib gradient ratio max', 
'GHI Clearsky GHI pvlib gradient second ratio', 
'GHI Clearsky GHI pvlib gradient second ratio mean', 
'GHI Clearsky GHI pvlib gradient second ratio std', 
'GHI Clearsky GHI pvlib gradient second ratio min', 
'GHI Clearsky GHI pvlib gradient second ratio max', 
'GHI Clearsky GHI pvlib line length ratio',
'GHI Clearsky GHI pvlib line length ratio gradient',
'GHI Clearsky GHI pvlib line length ratio gradient second'
]

target_cols = ['sky_status']

# Train/test on NSRDB data to find optimal parameters

In [6]:
import xgboost as xgb
# clf = xgb.XGBClassifier(**{'max_depth': 4, 'n_estimators': 500, 'learning_rate': 0.005, 'reg_lambda': 1}, n_jobs=4)
clf = xgb.XGBClassifier(n_jobs=4)

In [7]:
train = cs_detection.ClearskyDetection(nsrdb.df)
train.trim_dates('01-01-2010', '01-01-2015')
test = cs_detection.ClearskyDetection(nsrdb.df)
test.trim_dates('01-01-2015', None)

In [8]:
train.scale_model('GHI', 'Clearsky GHI pvlib', 'sky_status')

In [9]:
train.calc_all_window_metrics(train.df, 3, col1='GHI', col2='Clearsky GHI pvlib', overwrite=True)

In [10]:
from sklearn import model_selection
gscv = model_selection.GridSearchCV(clf, param_grid={'max_depth': [3, 4, 5], 
                                                     'n_estimators': [200, 400, 600], 
                                                     'learning_rate': [.1, .05, .01, .005, .001]})

In [11]:
gscv.fit(train.df[feature_cols].values, train.df[target_cols].values.flatten())

GridSearchCV(cv=None, error_score='raise',
       estimator=XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=1, gamma=0, learning_rate=0.1, max_delta_step=0,
       max_depth=3, min_child_weight=1, missing=None, n_estimators=100,
       n_jobs=4, nthread=None, objective='binary:logistic', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1),
       fit_params={}, iid=True, n_jobs=1,
       param_grid={'max_depth': [3, 4, 5], 'n_estimators': [200, 400, 600], 'learning_rate': [0.1, 0.05, 0.01, 0.005, 0.001]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score=True,
       scoring=None, verbose=0)

In [12]:
gscv.best_params_

{'learning_rate': 0.1, 'max_depth': 3, 'n_estimators': 400}

In [13]:
gscv.best_score_

0.9501300657174151

In [14]:
clf = gscv.best_estimator_

In [15]:
# clf = xgb.XGBClassifier(**{'max_depth': 6, 'n_estimators': 457, 'learning_rate': 0.007531383102591539}, n_jobs=4)

In [16]:
# clf.fit(train.df[feature_cols].values, train.df[target_cols].values.flatten())

In [17]:
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 3)
pred = pred.astype(bool)

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:800: RuntimeWarning:

Large scaling value.  Day will not be further assessed or scaled.

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:807: RuntimeWarning:

Scaling did not converge.



In [18]:
vis = visualize.Visualizer()
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(test.df['sky_status'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(test.df['sky_status'] == 1) & (~pred)]['GHI'], 'NSRDB clear only')
vis.add_circle_ser(test.df[(test.df['sky_status'] == 1) & (pred)]['GHI'], 'ML+NSRDB clear only')
vis.show()

In [19]:
cm = metrics.confusion_matrix(test.df['sky_status'].values, pred)
vis = visualize.Visualizer()
vis.plot_confusion_matrix(cm, labels=['cloudy', 'clear'])

In [20]:
print(metrics.f1_score(test.df['sky_status'].values, pred))

0.91321394511


# Train on all NSRDB data, test various freq of ground data

In [21]:
train = cs_detection.ClearskyDetection(nsrdb.df)
train.scale_model('GHI', 'Clearsky GHI pvlib', 'sky_status')
train.calc_all_window_metrics(train.df, 3, col1='GHI', col2='Clearsky GHI pvlib', overwrite=True)
clf.fit(train.df[feature_cols].values, train.df[target_cols].values.flatten())

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=1, gamma=0, learning_rate=0.1, max_delta_step=0,
       max_depth=3, min_child_weight=1, missing=None, n_estimators=400,
       n_jobs=4, nthread=None, objective='binary:logistic', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1)

## 30 min freq ground data

In [22]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')
test = cs_detection.ClearskyDetection(ground.df)

In [23]:
test.trim_dates('10-08-2015', '10-16-2015')

In [24]:
test.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [25]:
test.df = test.df[test.df.index.minute % 30 == 0]

In [26]:
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 3).astype(bool)

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:800: RuntimeWarning:

Large scaling value.  Day will not be further assessed or scaled.

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:807: RuntimeWarning:

Scaling did not converge.



In [27]:
vis = visualize.Visualizer()

In [28]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[pred]['GHI'], 'ML clear only')
# vis.add_circle_ser(test.df[(train.df['sky_status'] == 1) & (~pred)]['GHI'], 'NSRDB clear only')
# vis.add_circle_ser(test.df[(train.df['sky_status'] == 1) & (pred)]['GHI'], 'ML+NSRDB clear only')

In [29]:
vis.show()

## 15 min freq ground data

In [30]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')
test = cs_detection.ClearskyDetection(ground.df)

In [31]:
test.trim_dates('10-08-2015', '10-16-2015')

In [32]:
test.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [33]:
test.df = test.df[test.df.index.minute % 15 == 0]

In [34]:
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 5).astype(bool)

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:800: RuntimeWarning:

Large scaling value.  Day will not be further assessed or scaled.

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:807: RuntimeWarning:

Scaling did not converge.



In [35]:
vis = visualize.Visualizer()

In [36]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[pred]['GHI'], 'ML clear only')

In [37]:
vis.show()

## 10 min freq ground data

In [38]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')
test = cs_detection.ClearskyDetection(ground.df)

In [39]:
test.trim_dates('10-08-2015', '10-16-2015')

In [40]:
test.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [41]:
test.df = test.df[test.df.index.minute % 10 == 0]

In [42]:
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 7).astype(bool)

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:800: RuntimeWarning:

Large scaling value.  Day will not be further assessed or scaled.

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:807: RuntimeWarning:

Scaling did not converge.



In [43]:
vis = visualize.Visualizer()

In [44]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[pred]['GHI'], 'ML clear only')

In [45]:
vis.show()

## 5 min freq ground data

In [46]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')
test = cs_detection.ClearskyDetection(ground.df)

In [47]:
test.trim_dates('10-08-2015', '10-16-2015')

In [48]:
test.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [49]:
test.df = test.df[test.df.index.minute % 5 == 0]

In [50]:
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 13).astype(bool)

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:800: RuntimeWarning:

Large scaling value.  Day will not be further assessed or scaled.

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:807: RuntimeWarning:

Scaling did not converge.



In [51]:
vis = visualize.Visualizer()

In [52]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[pred]['GHI'], 'ML clear only')

In [53]:
vis.show()

## 1 min freq ground data

In [54]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')
test = cs_detection.ClearskyDetection(ground.df)

In [55]:
test.trim_dates('10-08-2015', '10-16-2015')

In [56]:
test.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [57]:
test.df = test.df[test.df.index.minute % 1 == 0]

In [58]:
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 61).astype(bool)

/Users/benellis/duramat/clearsky_detection/cs_detection_refactor.py:807: RuntimeWarning:

Scaling did not converge.



In [59]:
vis = visualize.Visualizer()

In [60]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[pred]['GHI'], 'ML clear only')

In [61]:
vis.show()

In [62]:
import pickle

In [63]:
with open('abq_trained.pkl', 'wb') as f:
    pickle.dump(clf, f)